<a href="https://colab.research.google.com/github/lahdeaho/colab-test/blob/master/traffic_analysis_1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## GPU Testaus and Initialisointi

* NVIDIA versio
* NVCC versio
* MXNET pitää asentaa oikealle CUDA versiolle (oletus 10)
* Liitos Google Driveen (mount) (työkansio)
* Liitos Azuren File Shareen (REST) (pitkäaikaissäilytys)
* MapBoxGL karttaa varten
* KeplerGL karttaa varten

In [0]:
!nvidia-smi

Fri May  3 06:12:08 2019       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 418.56       Driver Version: 410.79       CUDA Version: 10.0     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|===============================+======================+======================|
|   0  Tesla T4            Off  | 00000000:00:04.0 Off |                    0 |
| N/A   45C    P8    16W /  70W |      0MiB / 15079MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
                                                                               
+-----------------------------------------------------------------------------+
| Processes:                                                       GPU Memory |
|  GPU  

In [0]:
!nvcc --version

nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2018 NVIDIA Corporation
Built on Sat_Aug_25_21:08:01_CDT_2018
Cuda compilation tools, release 10.0, V10.0.130


In [0]:
!pip install mxnet-cu100 --pre

     |████████████████████████████████| 476.6MB 30kB/s 


In [0]:
# save model image file to Google Drive
from google.colab import drive
drive.mount('/content/gdrive')

In [0]:
!ls -la /content/gdrive/'My Drive'/'Colab Notebooks'

total 7
-rw------- 1 root root 6624 May  3 06:54 gpu-test-1.ipynb


In [0]:
!pip install azure-storage-file

     |████████████████████████████████| 51kB 6.8MB/s 
     |████████████████████████████████| 2.3MB 14.5MB/s 
     |████████████████████████████████| 102kB 40.2MB/s 


In [1]:
!pip install keplergl_jupyter

     |████████████████████████████████| 5.9MB 4.6MB/s 
  Stored in directory: /root/.cache/pip/wheels/06/f6/0d/08628337dd60c08bb3c2c11bb6e926a329ea8ea4e7c438694f
Successfully built keplergl-jupyter


In [36]:
!pip install mapboxgl

     |████████████████████████████████| 51kB 3.4MB/s 
  Stored in directory: /root/.cache/pip/wheels/43/3b/8c/3f6d7536b8bef26b7c3be5989f8103513eb949e50a4f9f81cf
Successfully built chroma-py


## Logiikan alku

In [0]:
from azure.storage.file import FileService
file_service = FileService(account_name='imagedatastorage', account_key='<accesskey>')

In [0]:
import numpy as np
import mxnet as mx

In [5]:
import keplergl_jupyter as keplergl
map_1 = keplergl.KeplerGl()
map_1

Documentation: https://github.com/uber/kepler.gl-jupyter/blob/master/README.md


KeplerGl()

In [9]:
shares = list(file_service.list_shares(include_snapshots=True))
for s in shares:
  print(s.name)

shared-files


In [0]:
generator = file_service.list_directories_and_files('shared-files/data/images/traffic/C0150200/img')
for f in generator:
    print(f.name)

In [0]:
#file_service.get_file_to_path()

### Kamera-asemat


In [0]:
import requests
import json
from pandas.io.json import json_normalize

In [0]:
response=requests.get('https://tie.digitraffic.fi/api/v1/data/camera-data')
data = response.json()
df_images = json_normalize(data['cameraStations'], 'cameraPresets')

In [0]:
response=requests.get('https://tie.digitraffic.fi/api/v1/metadata/camera-stations')
data = response.json()
df_meta = json_normalize(data['features'])

In [24]:
df_meta.columns

Index(['geometry.coordinates', 'geometry.type', 'id',
       'properties.annualMaintenanceTime', 'properties.cameraType',
       'properties.collectionInterval', 'properties.collectionStatus',
       'properties.coordinatesETRS89', 'properties.country', 'properties.id',
       'properties.liviId', 'properties.municipality',
       'properties.municipalityCode', 'properties.name', 'properties.names.en',
       'properties.names.fi', 'properties.names.sv',
       'properties.nearestWeatherStationId', 'properties.presets',
       'properties.province', 'properties.provinceCode', 'properties.purpose',
       'properties.repairMaintenanceTime',
       'properties.roadAddress.carriageway',
       'properties.roadAddress.carriagewayCode',
       'properties.roadAddress.contractArea',
       'properties.roadAddress.contractAreaCode',
       'properties.roadAddress.distanceFromRoadSectionStart',
       'properties.roadAddress.roadMaintenanceClass',
       'properties.roadAddress.roadNumber',
  

In [0]:
cameratypes = df_meta['properties.cameraType'].unique().tolist()

In [0]:
states = df_meta['properties.state'].unique().tolist()

In [30]:
response.content.decode('utf-8')

'{\n  "type" : "FeatureCollection",\n  "dataUpdatedTime" : "2019-05-03T08:00:43Z",\n  "dataLastCheckedTime" : "2019-05-03T08:00:43Z",\n  "features" : [ {\n    "type" : "Feature",\n    "id" : "1502",\n    "geometry" : {\n      "type" : "Point",\n      "type" : "Point",\n      "coordinates" : [ 25.616391299785636, 60.39023804760148, 0.0 ]\n    },\n    "properties" : {\n      "roadStationId" : 1502,\n      "id" : "C01502",\n      "name" : "vt7_Porvoo_Harabacka",\n      "cameraType" : "VMX_MPH",\n      "collectionInterval" : 720,\n      "collectionStatus" : "GATHERING",\n      "municipality" : "Porvoo",\n      "municipalityCode" : "638",\n      "province" : "Uusimaa",\n      "provinceCode" : "1",\n      "names" : {\n        "fi" : "Tie 7 Porvoo",\n        "sv" : "Väg 7 Borgå",\n        "en" : "Road 7 Porvoo"\n      },\n      "roadAddress" : {\n        "roadNumber" : 7,\n        "roadSection" : 8,\n        "distanceFromRoadSectionStart" : 3801,\n        "carriagewayCode" : 1,\n        "road

In [34]:
map_1 = keplergl.KeplerGl()
map_1

Documentation: https://github.com/uber/kepler.gl-jupyter/blob/master/README.md


KeplerGl()

In [33]:
map_1 = keplergl.KeplerGl(height=400, data={'data_1': response.content.decode('utf-8')})
map_1

Documentation: https://github.com/uber/kepler.gl-jupyter/blob/master/README.md


KeplerGl(data={'data_1': '{\n  "type" : "FeatureCollection",\n  "dataUpdatedTime" : "2019-05-03T08:00:43Z",\n …

In [0]:
import pandas as pd
from mapboxgl.utils import *
from mapboxgl.viz import *

In [0]:
geodata = {"type": "FeatureCollection","features": data['features']}
YlGnBu = {
    3: ["rgb(237,248,177)", "rgb(127,205,187)", "rgb(44,127,184)"],
    4: ["rgb(255,255,204)", "rgb(161,218,180)", "rgb(65,182,196)", "rgb(34,94,168)"],
    5: ["rgb(255,255,204)", "rgb(161,218,180)", "rgb(65,182,196)", "rgb(44,127,184)", "rgb(37,52,148)"],
    6: ["rgb(255,255,204)", "rgb(199,233,180)", "rgb(127,205,187)", "rgb(65,182,196)", "rgb(44,127,184)", "rgb(37,52,148)"],
    7: ["rgb(255,255,204)", "rgb(199,233,180)", "rgb(127,205,187)", "rgb(65,182,196)", "rgb(29,145,192)", "rgb(34,94,168)", "rgb(12,44,132)"],
    8: ["rgb(255,255,217)", "rgb(237,248,177)", "rgb(199,233,180)", "rgb(127,205,187)", "rgb(65,182,196)", "rgb(29,145,192)", "rgb(34,94,168)", "rgb(12,44,132)"],
    9: ["rgb(255,255,217)", "rgb(237,248,177)", "rgb(199,233,180)", "rgb(127,205,187)", "rgb(65,182,196)", "rgb(29,145,192)", "rgb(34,94,168)", "rgb(37,52,148)", "rgb(8,29,88)"]
}

In [94]:
df_meta.groupby(['properties.cameraType']).count()[['id']].sort_values('id', ascending=False)

id
properties.cameraType     
VAPIX                  465
BOSCH                   64
VMX_MPH                 52
VMX_MPC                 45
D_LINK                  26
ZAVIO                   23
HIKVISION               15
ENEO                     5

In [95]:
df_meta.groupby(['properties.state']).count()[['id']].sort_values('id', ascending=False)

id
properties.state             
OK                        393
OK_FAULT_DOUBT_CANCELLED   65
REPAIR_MAINTENANCE_DONE    17
REPAIR_INTERRUPTED         10
REPAIR_REQUEST_POSTED       3
FAULT_CONFIRMED             1
FAULT_DOUBT                 1

In [96]:
#mapbox token
token = "pk.eyJ1IjoibGFoZGVhaG8yIiwiYSI6IjJfd0pIaW8ifQ.rRUcK5QDBi71XiqNt5ZZ8Q"

category_color_stops = np.array(states + YlGnBu[len(states)]).reshape(2,-1).transpose().tolist()

viz = CircleViz(geodata, 
               access_token=token,
               height='800px',
               radius=5,
               label_property='id',
               color_property=None, 
               color_function_type='match',
               color_stops=category_color_stops
               )
viz.show()

In [79]:
geodata

{'features': [{'geometry': {'coordinates': [25.616391299785636,
     60.39023804760148,
     0.0],
    'type': 'Point'},
   'id': '1502',
   'properties': {'annualMaintenanceTime': None,
    'cameraType': 'VMX_MPH',
    'collectionInterval': 720,
    'collectionStatus': 'GATHERING',
    'coordinatesETRS89': [423740.0, 6695673.0, 0.0],
    'country': None,
    'id': 'C01502',
    'liviId': 'Livi1089373',
    'municipality': 'Porvoo',
    'municipalityCode': '638',
    'name': 'vt7_Porvoo_Harabacka',
    'names': {'en': 'Road 7 Porvoo',
     'fi': 'Tie 7 Porvoo',
     'sv': 'Väg 7 Borgå'},
    'nearestWeatherStationId': 1019,
    'presets': [{'cameraId': 'C01502',
      'direction': 'UNKNOWN',
      'directionCode': '0',
      'imageUrl': 'http://weathercam.digitraffic.fi/C0150200.jpg',
      'inCollection': True,
      'presentationName': 'Porvoo',
      'presetId': 'C0150200',
      'resolution': '704x576'},
     {'cameraId': 'C01502',
      'direction': 'INCREASING_DIRECTION',
      '